In [0]:
#%pyspark
from pyspark.sql.types import *
from pyspark.sql.functions import *

from pyspark.ml import *
from pyspark.ml.regression import LinearRegression , DecisionTreeRegressor, RandomForestRegressor, GBTRegressionModel, GBTRegressor

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.tuning import ParamGridBuilder, TrainValidationSplit, CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator

from pyspark.ml.feature import VectorIndexer
from pyspark.ml.feature import VectorAssembler, MinMaxScaler
from pyspark.ml.linalg import Vectors

from pyspark.ml.evaluation import BinaryClassificationEvaluator

from pyspark.sql import SparkSession
from pyspark.sql import functions as F

from pyspark.context import SparkContext
from pyspark.mllib.evaluation import MulticlassMetrics


In [0]:
#%pyspark
#PYSPARK_CLI = True
#if PYSPARK_CLI:
	#sc = SparkContext.getOrCreate()
	#spark = SparkSession(sc)

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2016_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Tut-Non Stdnt 0 0 null 10451 0 0 0 10451 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Lect-Ay-1/9|Teacher-Unex|Lect-Ay|Tut-Non Stdnt|Academic Appt 0 0 null 45855 0 215 21828 67898 7381 0 0 551 7932 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 3 0 0 null 5538 0 0 0 5538 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 1 0 0 null 6856 0 0 0 6856 0 0 0 892 892 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51278 89 0 0 51367 7178 0 0 7528 14706 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 28218 121 0 6239 34578 3950 0 0 3130 7080 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5280 0 0 0 5280 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 43927 147 0 500 44574 4557 0 0 6962 11519 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 26832 45 0 1000 27877 3756 0 0 12014 15770 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 11960 0 0 0 11960 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3718 0 0 0 3718 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5918 0 0 0 5918 0 0 0 892 892 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false fa

In [0]:
#%pyspark
#df.printSchema()

In [0]:
# Create a view or table

temp_table_name = "2016_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:

dftemp=df.select('EmployerName','Position','TotalWages', 'RegularPay', 'MaxPositionSalary', 'MinPositionSalary')
dftemp.show()

+--------------------+--------------------+----------+----------+-----------------+-----------------+
|        EmployerName|            Position|TotalWages|RegularPay|MaxPositionSalary|MinPositionSalary|
+--------------------+--------------------+----------+----------+-----------------+-----------------+
|University of Cal...|Acad Achievement ...|     10451|     10451|                0|                0|
|University of Cal...|Acad Achievement ...|     67898|     45855|                0|                0|
|University of Cal...|Acad Achievement ...|      5538|      5538|                0|                0|
|University of Cal...|Acad Achievement ...|      6856|      6856|                0|                0|
|University of Cal...|Acad Achievement ...|     51367|     51278|                0|                0|
|University of Cal...|Acad Achievement ...|     34578|     28218|                0|                0|
|University of Cal...|Acad Achievement ...|      5280|      5280|                0

In [0]:
%sql
select * from `2016_UniversityOfCalifornia_csv` 

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Tut-Non Stdnt 0 0 null 10451 0 0 0 10451 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Lect-Ay-1/9|Teacher-Unex|Lect-Ay|Tut-Non Stdnt|Academic Appt 0 0 null 45855 0 215 21828 67898 7381 0 0 551 7932 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 3 0 0 null 5538 0 0 0 5538 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 1 0 0 null 6856 0 0 0 6856 0 0 0 892 892 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51278 89 0 0 51367 7178 0 0 7528 14706 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 28218 121 0 6239 34578 3950 0 0 3130 7080 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5280 0 0 0 5280 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 43927 147 0 500 44574 4557 0 0 6962 11519 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 26832 45 0 1000 27877 3756 0 0 12014 15770 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 11960 0 0 0 11960 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3718 0 0 0 3718 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5918 0 0 0 5918 0 0 0 892 892 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false fa

In [0]:
df.take(10)

Out[7]: [Row(Year=2016, EmployerType='University of California', EmployerName='University of California, Berkeley', DepartmentOrSubdivision='UC- Berkeley', Position='Acad Achievement Cnslr 2', ElectedOfficial=False, Judicial=False, OtherPositions='Tut-Non Stdnt', MinPositionSalary=0, MaxPositionSalary=0, ReportedBaseWage=None, RegularPay=10451, OvertimePay=0, LumpSumPay=0, OtherPay=0, TotalWages=10451, DefinedBenefitPlanContribution=0, EmployeesRetirementCostCovered=0, DeferredCompensationPlan=0, HealthDentalVision=0, TotalRetirementAndHealthContribution=0, PensionFormula=None, EmployerURL='https://ucnet.universityofcalifornia.edu/compensation-and-benefits/', EmployerPopulation=None, LastUpdatedDate='08/22/2017', EmployerCounty='Alameda', SpecialDistrictActivities=None, IncludesUnfundedLiability=None, SpecialDistrictType=None),
 Row(Year=2016, EmployerType='University of California', EmployerName='University of California, Berkeley', DepartmentOrSubdivision='UC- Berkeley', Position='Ac

In [0]:
df_sql = spark.sql("select * from 2016_UniversityOfCalifornia_csv LIMIT 10")
display(df_sql) 

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Tut-Non Stdnt 0 0 null 10451 0 0 0 10451 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Lect-Ay-1/9|Teacher-Unex|Lect-Ay|Tut-Non Stdnt|Academic Appt 0 0 null 45855 0 215 21828 67898 7381 0 0 551 7932 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 3 0 0 null 5538 0 0 0 5538 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false Stdt 1 0 0 null 6856 0 0 0 6856 0 0 0 892 892 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51278 89 0 0 51367 7178 0 0 7528 14706 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 28218 121 0 6239 34578 3950 0 0 3130 7080 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5280 0 0 0 5280 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 43927 147 0 500 44574 4557 0 0 6962 11519 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 26832 45 0 1000 27877 3756 0 0 12014 15770 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null 2016 University of California University of California, Berkeley UC- Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 11960 0 0 0 11960 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 08/22/2017 Alameda null null null

In [0]:
df.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- DepartmentOrSubdivision: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- ElectedOfficial: boolean (nullable = true)
 |-- Judicial: boolean (nullable = true)
 |-- OtherPositions: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- DefinedBenefitPlanContribution: integer (nullable = true)
 |-- EmployeesRetirementCostCovered: integer (nullable = true)
 |-- DeferredCompensationPlan: integer (nullable = true)
 |-- HealthDentalVision: integer (nullable = true)
 |-- TotalRetirementAndHealthContribution: i

In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
display(df2)

Year EmployerType EmployerName Position MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages LastUpdatedDate EmployerCounty 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 10451 0 0 0 10451 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 45855 0 215 21828 67898 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 5538 0 0 0 5538 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 6856 0 0 0 6856 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 51278 89 0 0 51367 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 28218 121 0 6239 34578 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 5280 0 0 0 5280 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 43927 147 0 500 44574 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 26832 45 0 1000 27877 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 11960 0 0 0 11960 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 3718 0 0 0 3718 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 5918 0 0 0 5918 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 52458 0 0 2000 54458 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 49899 0 0 500 50399 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 52333 0 0 2000 54333 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 3496 0 0 0 3496 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 3124 0 0 637 3761 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 57492 0 0 3320 60812 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 66620 0 0 0 66620 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 63545 0 0 0 63545 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 62449 0 0 3000 65449 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 64856 0 0 0 64856 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 61513 0 0 0 61513 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 34731 0 0 8105 42836 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 59240 0 0 500 59740 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 22020 0 0 1274 23294 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 81030 0 0 500 81530 08/22/2017 Alameda 2016 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 88400 0 0 0 88400 0

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     10451|          0|         0|       0|     10451|     08/22/2017|       Alameda|
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     45855|          0|       215|   21828|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 204029 Testing Rows: 87112


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3124|          0|         0|     637|      3761|     08/22/2017|       Alameda|[3124.0,3761.0,0....|
|2016|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_e1e5790786d4, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 87637.0)
     If (feature 1 <= 32216.5)
      Predict: 8692.799119946936
     Else (feature 1 > 32216.5)
      If (feature 1 <= 65231.0)
       Predict: 48920.072865001355
      Else (feature 1 > 65231.0)
       If (feature 1 <= 149173.5)
        If (feature 0 <= 77209.0)
         Predict: 75377.37864587239
        Else (feature 0 > 77209.0)
         Predict: 87965.921812596
       Else (feature 1 > 149173.5)
        If (feature 1 <= 194468.0)
         Predict: 168304.48167539266
        Else (feature 1 > 194468.0)
         Predict: 276897.3879310345
    Else (feature 0 > 87637.0)
     Predict: 164952.0504329141
  Tree 1 (weight 1.0):
    If (feature 1 <= 107385.0)
     If (feature 0 <= 35613.5)
      If (feature 0 <= 13065.5)
       Predict: 4390.5482051032095
      Else (feature 0 > 13065.5)
       If (feature 1 <= 27423.0)
        Predict: 20357

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.531864 
 
 
 1 
 TotalWages 
 0.468136 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3496.0,3496.0,0....|17729.532142253538|      3496|
|[6856.0,6856.0,0....| 20080.29986356784|      6856|
|[26832.0,27877.0,...| 32946.03723818155|     27877|
|[52333.0,54333.0,...| 52122.98707746277|     54333|
|[62449.0,65449.0,...| 62366.60192141829|     65449|
|[63545.0,63545.0,...|58327.605986506635|     63545|
|[72786.0,72786.0,...| 66708.09057641658|     72786|
|[74155.0,74155.0,...| 66708.09057641658|     74155|
|[76949.0,77449.0,...| 66708.09057641658|     77449|
|[78392.0,78392.0,...|   71216.208479207|     78392|
|[81030.0,81530.0,...|   71216.208479207|     81530|
|[84337.0,84837.0,...| 73473.63229479629|     84837|
|[72018.0,82607.0,...| 69546.54569003316|     82607|
|[86199.0,86699.0,...| 73473.63229479629|     86699|
|[95021.0,95021.0,...| 95644.70381980424|     95021|
|[99867.0,108968.0...|114374.61008667419|    1

In [0]:
display(predicted)

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(3496.0, 3496.0, 0.0, 0.0)) 17729.532142253538 3496 Map(vectorType -> dense, length -> 4, values -> List(6856.0, 6856.0, 0.0, 0.0)) 20080.29986356784 6856 Map(vectorType -> dense, length -> 4, values -> List(26832.0, 27877.0, 0.0, 0.0)) 32946.03723818155 27877 Map(vectorType -> dense, length -> 4, values -> List(52333.0, 54333.0, 0.0, 0.0)) 52122.98707746277 54333 Map(vectorType -> dense, length -> 4, values -> List(62449.0, 65449.0, 0.0, 0.0)) 62366.60192141829 65449 Map(vectorType -> dense, length -> 4, values -> List(63545.0, 63545.0, 0.0, 0.0)) 58327.605986506635 63545 Map(vectorType -> dense, length -> 4, values -> List(72786.0, 72786.0, 0.0, 0.0)) 66708.09057641658 72786 Map(vectorType -> dense, length -> 4, values -> List(74155.0, 74155.0, 0.0, 0.0)) 66708.09057641658 74155 Map(vectorType -> dense, length -> 4, values -> List(76949.0, 77449.0, 0.0, 0.0)) 66708.09057641658 77449 Map(vectorType -> dense, length -> 4, values -> List(78392.0, 78392.0, 0.0, 0.0)) 71216.208479207 78392 Map(vectorType -> dense, length -> 4, values -> List(81030.0, 81530.0, 0.0, 0.0)) 71216.208479207 81530 Map(vectorType -> dense, length -> 4, values -> List(84337.0, 84837.0, 0.0, 0.0)) 73473.63229479629 84837 Map(vectorType -> dense, length -> 4, values -> List(72018.0, 82607.0, 0.0, 0.0)) 69546.54569003316 82607 Map(vectorType -> dense, length -> 4, values -> List(86199.0, 86699.0, 0.0, 0.0)) 73473.63229479629 86699 Map(vectorType -> dense, length -> 4, values -> List(95021.0, 95021.0, 0.0, 0.0)) 95644.70381980424 95021 Map(vectorType -> dense, length -> 4, values -> List(99867.0, 108968.0, 0.0, 0.0)) 114374.61008667419 108968 Map(vectorType -> dense, length -> 4, values -> List(27360.0, 27360.0, 0.0, 0.0)) 31699.17636558307 27360 Map(vectorType -> dense, length -> 4, values -> List(45365.0, 45865.0, 0.0, 0.0)) 50218.415097691155 45865 Map(vectorType -> dense, length -> 4, values -> List(60626.0, 60626.0, 0.0, 0.0)) 56346.07861184521 60626 Map(vectorType -> dense, length -> 4, values -> List(68902.0, 69171.0, 0.0, 0.0)) 66708.09057641658 69171 Map(vectorType -> dense, length -> 4, values -> List(24882.0, 27456.0, 0.0, 0.0)) 31482.503656551864 27456 Map(vectorType -> dense, length -> 4, values -> List(27663.0, 27663.0, 0.0, 0.0)) 32946.03723818155 27663 Map(vectorType -> dense, length -> 4, values -> List(40419.0, 42423.0, 0.0, 0.0)) 48602.681273829156 42423 Map(vectorType -> dense, length -> 4, values -> List(54825.0, 54825.0, 0.0, 0.0)) 53754.841663962616 54825 Map(vectorType -> dense, length -> 4, values -> List(55425.0, 56047.0, 0.0, 0.0)) 53754.841663962616 56047 Map(vectorType -> dense, length -> 4, values -> List(72992.0, 72992.0, 0.0, 0.0)) 66708.09057641658 72992 Map(vectorType -> dense, length -> 4, values -> List(75500.0, 75500.0, 0.0, 0.0)) 66708.09057641658 75500 Map(vectorType -> dense, length -> 4, values -> List(75783.0, 75783.0, 0.0, 0.0)) 66708.09057641658 75783 Map(vectorType -> dense, length -> 4, values -> List(75916.0, 75916.0, 0.0, 0.0)) 66708.09057641658 75916 Map(vectorType -> dense, length -> 4, values -> List(77274.0, 77274.0, 0.0, 0.0)) 71216.208479207 77274 Map(vectorType -> dense, length -> 4, values -> List(78026.0, 78026.0, 0.0, 0.0)) 71216.208479207 78026 Map(vectorType -> dense, length -> 4, values -> List(84803.0, 84803.0, 0.0, 0.0)) 73473.63229479629 84803 Map(vectorType -> dense, length -> 4, values -> List(85944.0, 85944.0, 0.0, 0.0)) 73473.63229479629 85944 Map(vectorType -> dense, length -> 4, values -> List(87603.0, 87603.0, 0.0, 0.0)) 73473.63229479629 87603 Map(vectorType -> dense, length -> 4, values -> List(89714.0, 89714.0, 0.0, 0.0)) 95644.70381980424 89714 Map(vectorType -> dense, length -> 4, values -> List(91184.0, 91184.0, 0.0, 0.0)) 95644.70381980424 91184 Map(vectorType -> dense, length -> 4, values -> List(93375.0, 93375.0, 0.0, 0.0)) 95644.70381980424 93375 Map(vectorType -> dense, length -> 4, values -> List(9

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.711781
RMSE: 36745.611545


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     10451|          0|         0|       0|     10451|     08/22/2017|       Alameda|
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     45855|          0|       215|   21828|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 203954 Testing Rows: 87187


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3124|          0|         0|     637|      3761|     08/22/2017|       Alameda|[3124.0,3761.0,0....|
|2016|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      5280|          0|         0|       0|      5280|     08/22/2017|       Alameda|
|2016|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     26832|         45|         0|    1000|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[5280.0,5280.0,0....| 6640.058316256844|      5280|
|[26832.0,27877.0,...|22183.493908522214|     27877|
|[28218.0,34578.0,...|22183.493908522214|     34578|
|[49899.0,50399.0,...|52873.837345888765|     50399|
|[51278.0,51367.0,...|52873.837345888765|     51367|
|[52333.0,54333.0,...|52873.837345888765|     54333|
|[52458.0,54458.0,...|52873.837345888765|     54458|
|[22020.0,23294.0,...|22183.493908522214|     23294|
|[34731.0,42836.0,...|52873.837345888765|     42836|
|[57492.0,60812.0,...|59934.348438893096|     60812|
|[78392.0,78392.0,...|  75088.8638324209|     78392|
|[81849.0,81849.0,...| 82878.60630495416|     81849|
|[88400.0,88400.0,...| 82878.60630495416|     88400|
|[85963.0,85963.0,...| 82878.60630495416|     85963|
|[86199.0,86699.0,...| 82878.60630495416|     86699|
|[108755.0,109255....|130474.06919084006|    1

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[5280.0,5280.0,0....| 6640.058316256844|      5280|
|[26832.0,27877.0,...|22183.493908522214|     27877|
|[28218.0,34578.0,...|22183.493908522214|     34578|
|[49899.0,50399.0,...|52873.837345888765|     50399|
|[51278.0,51367.0,...|52873.837345888765|     51367|
|[52333.0,54333.0,...|52873.837345888765|     54333|
|[52458.0,54458.0,...|52873.837345888765|     54458|
|[22020.0,23294.0,...|22183.493908522214|     23294|
|[34731.0,42836.0,...|52873.837345888765|     42836|
|[57492.0,60812.0,...|59934.348438893096|     60812|
|[78392.0,78392.0,...|  75088.8638324209|     78392|
|[81849.0,81849.0,...| 82878.60630495416|     81849|
|[88400.0,88400.0,...| 82878.60630495416|     88400|
|[85963.0,85963.0,...| 82878.60630495416|     85963|
|[86199.0,86699.0,...| 82878.60630495416|     86699|
|[108755.0,109255....|130474.06919084006|    1

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.855332
RMSE: 25870.083607


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[5280.0,5280.0,0....| 4952.948345922286|      5280|
|[26832.0,27877.0,...|28209.343333776596|     27877|
|[28218.0,34578.0,...|34030.864906017676|     34578|
|[49899.0,50399.0,...|49473.106158167946|     50399|
|[51278.0,51367.0,...| 51996.52424631498|     51367|
|[52333.0,54333.0,...| 51996.52424631498|     54333|
|[52458.0,54458.0,...| 53145.52138641594|     54458|
|[22020.0,23294.0,...| 23500.98849304948|     23294|
|[34731.0,42836.0,...| 43764.64907103097|     42836|
|[57492.0,60812.0,...|60762.515300535604|     60812|
|[78392.0,78392.0,...| 76036.02783937224|     78392|
|[81849.0,81849.0,...| 85246.26305104198|     81849|
|[88400.0,88400.0,...| 86959.70913057747|     88400|
|[85963.0,85963.0,...| 86959.70913057747|     85963|
|[86199.0,86699.0,...| 86959.70913057747|     86699|
|[108755.0,109255....|112928.58487830084|    1

In [0]:
####CODE BREAK for 2015

#UC2015

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2015_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Acad Achievement Cnslr 3 0 0 null 52541 0 0 2320 54861 7540 0 0 7782 15322 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Teacher-Unex 0 0 null 4906 0 0 4140 9046 0 0 0 0 0 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1126 0 0 0 1126 0 0 0 0 0 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47593 787 0 500 48880 6663 0 0 7260 13923 2.5% @ 60 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51624 0 0 0 51624 7227 0 0 7260 14487 2.5% @ 60 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 41739 0 0 0 41739 4449 0 0 16572 21021 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1058 0 0 0 1058 148 0 0 2170 2318 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 2258 3066 0 2264 7588 316 0 0 0 316 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 48371 275 0 0 48646 6771 0 0 2567 9338 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47080 0 0 0 47080 3887 0 0 7863 11750 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 28980 0 0 0 28980 1322 0 0 5949 7271 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 24312 0 0 0 24312 3403 0 0 3425 6828 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Ac

In [0]:
# Create a view or table

temp_table_name = "2015_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
display(df2)

Year EmployerType EmployerName Position MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages LastUpdatedDate EmployerCounty 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 52541 0 0 2320 54861 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 4906 0 0 4140 9046 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 1126 0 0 0 1126 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 47593 787 0 500 48880 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 51624 0 0 0 51624 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 41739 0 0 0 41739 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 1058 0 0 0 1058 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 2258 3066 0 2264 7588 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 48371 275 0 0 48646 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 47080 0 0 0 47080 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 28980 0 0 0 28980 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 24312 0 0 0 24312 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 16560 0 0 0 16560 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 7920 0 0 0 7920 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 56413 0 0 500 56913 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 46451 2521 0 2000 50972 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 56454 0 0 0 56454 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 57739 0 0 0 57739 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 76296 0 0 0 76296 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 58425 0 0 500 58925 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 51009 0 0 623 51632 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 58307 0 0 0 58307 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 86666 0 0 0 86666 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 63345 0 0 0 63345 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 61074 0 0 500 61574 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 48455 0 0 4344 52799 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 70601 0 0 0 70601 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 80627 0 0 0 80627 07/22/20

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     52541|          0|         0|    2320|     54861|     07/22/2016|       Alameda|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4906|          0|         0|    4140|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 197530 Testing Rows: 83985


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1058|          0|         0|       0|      1058|     07/22/2016|       Alameda|[1058.0,1058.0,0....|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_1106770cb4ee, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 83041.0)
     If (feature 1 <= 30575.0)
      Predict: 8253.0935677048
     Else (feature 1 > 30575.0)
      If (feature 1 <= 62092.5)
       Predict: 46666.84077825035
      Else (feature 1 > 62092.5)
       If (feature 1 <= 183778.5)
        If (feature 1 <= 88850.0)
         Predict: 72351.97757149447
        Else (feature 1 > 88850.0)
         Predict: 105473.07783505155
       Else (feature 1 > 183778.5)
        Predict: 313319.8348623853
    Else (feature 0 > 83041.0)
     Predict: 156746.4126429479
  Tree 1 (weight 1.0):
    If (feature 1 <= 101859.5)
     If (feature 0 <= 33948.5)
      If (feature 0 <= 13162.0)
       Predict: 4346.265818059652
      Else (feature 0 > 13162.0)
       If (feature 1 <= 25857.0)
        Predict: 19670.304643074036
       Else (feature 1 > 25857.0)
        If (feature 1 <= 44676.5)
         Predict: 30949.2103

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.536236 
 
 
 1 
 TotalWages 
 0.463764 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[41739.0,41739.0,...| 46758.55159184633|     41739|
|[47080.0,47080.0,...|49106.899083382785|     47080|
|[47593.0,48880.0,...|49106.899083382785|     48880|
|[48371.0,48646.0,...|49106.899083382785|     48646|
|[52541.0,54861.0,...| 51435.71587458509|     54861|
|[56413.0,56913.0,...|  53902.8815233195|     56913|
|[58307.0,58307.0,...|54647.625853581354|     58307|
|[86666.0,86666.0,...| 90843.33702998384|     86666|
|[83686.0,83686.0,...| 90843.33702998384|     83686|
|[111047.0,111047....|109273.12504649072|    111047|
|[2781.0,2781.0,0....| 16428.52012111864|      2781|
|[10465.0,10465.0,...|20816.134551908766|     10465|
|[26856.0,26856.0,...| 31439.14233822204|     26856|
|[52744.0,52744.0,...| 51435.71587458509|     52744|
|[54994.0,55994.0,...|  53902.8815233195|     55994|
|[56273.0,56273.0,...|  53902.8815233195|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(41739.0, 41739.0, 0.0, 0.0)) 46758.55159184633 41739 Map(vectorType -> dense, length -> 4, values -> List(47080.0, 47080.0, 0.0, 0.0)) 49106.899083382785 47080 Map(vectorType -> dense, length -> 4, values -> List(47593.0, 48880.0, 0.0, 0.0)) 49106.899083382785 48880 Map(vectorType -> dense, length -> 4, values -> List(48371.0, 48646.0, 0.0, 0.0)) 49106.899083382785 48646 Map(vectorType -> dense, length -> 4, values -> List(52541.0, 54861.0, 0.0, 0.0)) 51435.71587458509 54861 Map(vectorType -> dense, length -> 4, values -> List(56413.0, 56913.0, 0.0, 0.0)) 53902.8815233195 56913 Map(vectorType -> dense, length -> 4, values -> List(58307.0, 58307.0, 0.0, 0.0)) 54647.625853581354 58307 Map(vectorType -> dense, length -> 4, values -> List(86666.0, 86666.0, 0.0, 0.0)) 90843.33702998384 86666 Map(vectorType -> dense, length -> 4, values -> List(83686.0, 83686.0, 0.0, 0.0)) 90843.33702998384 83686 Map(vectorType -> dense, length -> 4, values -> List(111047.0, 111047.0, 0.0, 0.0)) 109273.12504649072 111047 Map(vectorType -> dense, length -> 4, values -> List(2781.0, 2781.0, 0.0, 0.0)) 16428.52012111864 2781 Map(vectorType -> dense, length -> 4, values -> List(10465.0, 10465.0, 0.0, 0.0)) 20816.134551908766 10465 Map(vectorType -> dense, length -> 4, values -> List(26856.0, 26856.0, 0.0, 0.0)) 31439.14233822204 26856 Map(vectorType -> dense, length -> 4, values -> List(52744.0, 52744.0, 0.0, 0.0)) 51435.71587458509 52744 Map(vectorType -> dense, length -> 4, values -> List(54994.0, 55994.0, 0.0, 0.0)) 53902.8815233195 55994 Map(vectorType -> dense, length -> 4, values -> List(56273.0, 56273.0, 0.0, 0.0)) 53902.8815233195 56273 Map(vectorType -> dense, length -> 4, values -> List(60880.0, 61989.0, 0.0, 0.0)) 54647.625853581354 61989 Map(vectorType -> dense, length -> 4, values -> List(63398.0, 63398.0, 0.0, 0.0)) 58696.253777992635 63398 Map(vectorType -> dense, length -> 4, values -> List(63549.0, 63676.0, 0.0, 0.0)) 58696.253777992635 63676 Map(vectorType -> dense, length -> 4, values -> List(65024.0, 65024.0, 0.0, 0.0)) 64144.124169469695 65024 Map(vectorType -> dense, length -> 4, values -> List(69285.0, 69285.0, 0.0, 0.0)) 64144.124169469695 69285 Map(vectorType -> dense, length -> 4, values -> List(13943.0, 14183.0, 0.0, 0.0)) 24096.24430321642 14183 Map(vectorType -> dense, length -> 4, values -> List(33497.0, 33497.0, 0.0, 0.0)) 39932.81273809664 33497 Map(vectorType -> dense, length -> 4, values -> List(41866.0, 50898.0, 0.0, 0.0)) 47551.34644996253 50898 Map(vectorType -> dense, length -> 4, values -> List(49994.0, 92266.0, 0.0, 0.0)) 57323.18768062177 92266 Map(vectorType -> dense, length -> 4, values -> List(57159.0, 60103.0, 0.0, 0.0)) 53902.8815233195 60103 Map(vectorType -> dense, length -> 4, values -> List(61010.0, 61010.0, 0.0, 0.0)) 54647.625853581354 61010 Map(vectorType -> dense, length -> 4, values -> List(65293.0, 65293.0, 0.0, 0.0)) 64144.124169469695 65293 Map(vectorType -> dense, length -> 4, values -> List(68147.0, 68147.0, 0.0, 0.0)) 64144.124169469695 68147 Map(vectorType -> dense, length -> 4, values -> List(73504.0, 73504.0, 0.0, 0.0)) 65808.78243721211 73504 Map(vectorType -> dense, length -> 4, values -> List(75992.0, 75992.0, 0.0, 0.0)) 65808.78243721211 75992 Map(vectorType -> dense, length -> 4, values -> List(77987.0, 82315.0, 0.0, 0.0)) 68016.42846707985 82315 Map(vectorType -> dense, length -> 4, values -> List(82048.0, 82548.0, 0.0, 0.0)) 68016.42846707985 82548 Map(vectorType -> dense, length -> 4, values -> List(82554.0, 83054.0, 0.0, 0.0)) 68016.42846707985 83054 Map(vectorType -> dense, length -> 4, values -> List(87736.0, 89736.0, 0.0, 0.0)) 90843.33702998384 89736 Map(vectorType -> dense, length -> 4, values -> List(76623.0, 76623.0, 0.0, 0.0)) 65808.78243721211 76623 Map(vectorType -> dense, length -> 4, values -> List(87097.0, 90097.0, 0.0, 0.0)) 90843.33702998384 90097 Map(vectorType -> dense, length -> 4, va

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.721017
RMSE: 34696.848348


In [0]:
#GBT 2015


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     52541|          0|         0|    2320|     54861|     07/22/2016|       Alameda|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4906|          0|         0|    4140|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 197101 Testing Rows: 84414


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1126|          0|         0|       0|      1126|     07/22/2016|       Alameda|[1126.0,1126.0,0....|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1058.0,1058.0,0....|1130.2103379908597|      1058|
|[28980.0,28980.0,...|28273.969705467433|     28980|
|[41739.0,41739.0,...| 42217.28601568292|     41739|
|[51624.0,51624.0,...| 51414.73225784725|     51624|
|[52541.0,54861.0,...|55246.955444758445|     54861|
|[56413.0,56913.0,...| 56545.76860236969|     56913|
|[58307.0,58307.0,...| 59096.58163241763|     58307|
|[58425.0,58925.0,...| 59096.58163241763|     58925|
|[44694.0,75319.0,...| 72918.15323084239|     75319|
|[48455.0,52799.0,...| 50149.15169448764|     52799|
|[61074.0,61574.0,...| 60579.08816480211|     61574|
|[63345.0,63345.0,...|   65891.359818142|     63345|
|[66806.0,66806.0,...| 67079.92170917279|     66806|
|[68077.0,68577.0,...| 67079.92170917279|     68577|
|[72701.0,72701.0,...| 72974.13666881989|     72701|
|[72701.0,73201.0,...| 72974.13666881989|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1058.0,1058.0,0....|1130.2103379908597|      1058|
|[28980.0,28980.0,...|28273.969705467433|     28980|
|[41739.0,41739.0,...| 42217.28601568292|     41739|
|[51624.0,51624.0,...| 51414.73225784725|     51624|
|[52541.0,54861.0,...|55246.955444758445|     54861|
|[56413.0,56913.0,...| 56545.76860236969|     56913|
|[58307.0,58307.0,...| 59096.58163241763|     58307|
|[58425.0,58925.0,...| 59096.58163241763|     58925|
|[44694.0,75319.0,...| 72918.15323084239|     75319|
|[48455.0,52799.0,...| 50149.15169448764|     52799|
|[61074.0,61574.0,...| 60579.08816480211|     61574|
|[63345.0,63345.0,...|   65891.359818142|     63345|
|[66806.0,66806.0,...| 67079.92170917279|     66806|
|[68077.0,68577.0,...| 67079.92170917279|     68577|
|[72701.0,72701.0,...| 72974.13666881989|     72701|
|[72701.0,73201.0,...| 72974.13666881989|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.804209
RMSE: 30357.106044


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1058.0,1058.0,0....|1130.2103379908597|      1058|
|[28980.0,28980.0,...|28273.969705467433|     28980|
|[41739.0,41739.0,...| 42217.28601568292|     41739|
|[51624.0,51624.0,...| 51414.73225784725|     51624|
|[52541.0,54861.0,...|55246.955444758445|     54861|
|[56413.0,56913.0,...| 56545.76860236969|     56913|
|[58307.0,58307.0,...| 59096.58163241763|     58307|
|[58425.0,58925.0,...| 59096.58163241763|     58925|
|[44694.0,75319.0,...| 72918.15323084239|     75319|
|[48455.0,52799.0,...| 50149.15169448764|     52799|
|[61074.0,61574.0,...| 60579.08816480211|     61574|
|[63345.0,63345.0,...|   65891.359818142|     63345|
|[66806.0,66806.0,...| 67079.92170917279|     66806|
|[68077.0,68577.0,...| 67079.92170917279|     68577|
|[72701.0,72701.0,...| 72974.13666881989|     72701|
|[72701.0,73201.0,...| 72974.13666881989|     

In [0]:
#### Code Break for 2017

#UC 2017

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2017_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2017_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Tut-Non Gship 0 0 null 14572 0 0 500 15072 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 15283 376 0 0 15659 1835 0 0 4226 6061 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 27410 0 0 500 27910 3837 0 0 12386 16223 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3410 0 0 0 3410 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6215 0 0 0 6215 0 0 0 1295 1295 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 4 0 0 null 20064 0 0 1000 21064 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 48176 1313 0 0 49489 5132 0 0 15000 20132 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 4004 0 0 0 4004 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51220 0 0 0 51220 7170 0 0 25099 32269 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 9438 0 0 0 9438 0 0 0 2035 2035 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 31039 0 0 0 31039 4345 0 0 4610 8955 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 49638 386 0 500 50524 6949 0 0 9080 16029 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6193 0 

In [0]:
# Create a view or table

temp_table_name = "2017_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     14572|          0|         0|     500|     15072|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     15283|        376|         0|       0|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 208542 Testing Rows: 89524


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4004|          0|         0|       0|      4004|     09/25/2018|       Alameda|[4004.0,4004.0,0....|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_e01e9c0f35cf, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 90298.0)
     If (feature 1 <= 33527.0)
      Predict: 9028.342807939984
     Else (feature 1 > 33527.0)
      If (feature 1 <= 67532.5)
       Predict: 50890.70833971596
      Else (feature 1 > 67532.5)
       If (feature 1 <= 160461.5)
        If (feature 0 <= 79386.0)
         Predict: 78028.26490369918
        Else (feature 0 > 79386.0)
         Predict: 90646.20349854228
       Else (feature 1 > 160461.5)
        If (feature 0 <= 36665.0)
         Predict: 343455.03846153844
        Else (feature 0 > 36665.0)
         Predict: 221586.74308300397
    Else (feature 0 > 90298.0)
     Predict: 169656.23394790932
  Tree 1 (weight 1.0):
    If (feature 1 <= 113457.0)
     If (feature 0 <= 36665.0)
      If (feature 0 <= 13281.5)
       Predict: 4506.312284229525
      Else (feature 0 > 13281.5)
       If (feature 1 <= 28137.0)
        Predict: 20898

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.533562 
 
 
 1 
 TotalWages 
 0.466438 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3410.0,3410.0,0....| 18219.99745197342|      3410|
|[9438.0,9438.0,0....|21338.855034277753|      9438|
|[51220.0,51220.0,...|53245.869744880685|     51220|
|[53643.0,54143.0,...|53245.869744880685|     54143|
|[63588.0,63588.0,...|   60083.510668498|     63588|
|[66196.0,66196.0,...|   60083.510668498|     66196|
|[67996.0,67996.0,...|65365.476760179925|     67996|
|[15552.0,17428.0,...|27936.569142314984|     17428|
|[91125.0,91125.0,...| 97942.57629518774|     91125|
|[72396.0,73396.0,...| 69531.72503996565|     73396|
|[91061.0,92061.0,...| 97942.57629518774|     92061|
|[92026.0,92026.0,...| 97942.57629518774|     92026|
|[97522.0,99522.0,...|  99990.3549342174|     99522|
|[45224.0,51812.0,...| 51087.34617727752|     51812|
|[2344.0,2344.0,0....|17695.252782813288|      2344|
|[47196.0,47196.0,...| 51772.87680064512|     

In [0]:
display(predicted)

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(3410.0, 3410.0, 0.0, 0.0)) 18219.99745197342 3410 Map(vectorType -> dense, length -> 4, values -> List(9438.0, 9438.0, 0.0, 0.0)) 21338.855034277753 9438 Map(vectorType -> dense, length -> 4, values -> List(51220.0, 51220.0, 0.0, 0.0)) 53245.869744880685 51220 Map(vectorType -> dense, length -> 4, values -> List(53643.0, 54143.0, 0.0, 0.0)) 53245.869744880685 54143 Map(vectorType -> dense, length -> 4, values -> List(63588.0, 63588.0, 0.0, 0.0)) 60083.510668498 63588 Map(vectorType -> dense, length -> 4, values -> List(66196.0, 66196.0, 0.0, 0.0)) 60083.510668498 66196 Map(vectorType -> dense, length -> 4, values -> List(67996.0, 67996.0, 0.0, 0.0)) 65365.476760179925 67996 Map(vectorType -> dense, length -> 4, values -> List(15552.0, 17428.0, 0.0, 0.0)) 27936.569142314984 17428 Map(vectorType -> dense, length -> 4, values -> List(91125.0, 91125.0, 0.0, 0.0)) 97942.57629518774 91125 Map(vectorType -> dense, length -> 4, values -> List(72396.0, 73396.0, 0.0, 0.0)) 69531.72503996565 73396 Map(vectorType -> dense, length -> 4, values -> List(91061.0, 92061.0, 0.0, 0.0)) 97942.57629518774 92061 Map(vectorType -> dense, length -> 4, values -> List(92026.0, 92026.0, 0.0, 0.0)) 97942.57629518774 92026 Map(vectorType -> dense, length -> 4, values -> List(97522.0, 99522.0, 0.0, 0.0)) 99990.3549342174 99522 Map(vectorType -> dense, length -> 4, values -> List(45224.0, 51812.0, 0.0, 0.0)) 51087.34617727752 51812 Map(vectorType -> dense, length -> 4, values -> List(2344.0, 2344.0, 0.0, 0.0)) 17695.252782813288 2344 Map(vectorType -> dense, length -> 4, values -> List(47196.0, 47196.0, 0.0, 0.0)) 51772.87680064512 47196 Map(vectorType -> dense, length -> 4, values -> List(59977.0, 59977.0, 0.0, 0.0)) 59257.32633920309 59977 Map(vectorType -> dense, length -> 4, values -> List(60255.0, 60255.0, 0.0, 0.0)) 59257.32633920309 60255 Map(vectorType -> dense, length -> 4, values -> List(62893.0, 62893.0, 0.0, 0.0)) 59257.32633920309 62893 Map(vectorType -> dense, length -> 4, values -> List(64896.0, 64896.0, 0.0, 0.0)) 60083.510668498 64896 Map(vectorType -> dense, length -> 4, values -> List(12716.0, 12716.0, 0.0, 0.0)) 22151.432944170923 12716 Map(vectorType -> dense, length -> 4, values -> List(45441.0, 52810.0, 0.0, 0.0)) 51087.34617727752 52810 Map(vectorType -> dense, length -> 4, values -> List(53708.0, 66940.0, 0.0, 0.0)) 54129.72310253931 66940 Map(vectorType -> dense, length -> 4, values -> List(68823.0, 68823.0, 0.0, 0.0)) 65365.476760179925 68823 Map(vectorType -> dense, length -> 4, values -> List(77153.0, 78153.0, 0.0, 0.0)) 70458.31546831736 78153 Map(vectorType -> dense, length -> 4, values -> List(88025.0, 88025.0, 0.0, 0.0)) 75140.65622648112 88025 Map(vectorType -> dense, length -> 4, values -> List(87861.0, 88361.0, 0.0, 0.0)) 75140.65622648112 88361 Map(vectorType -> dense, length -> 4, values -> List(90443.0, 90443.0, 0.0, 0.0)) 97942.57629518774 90443 Map(vectorType -> dense, length -> 4, values -> List(93503.0, 94003.0, 0.0, 0.0)) 97942.57629518774 94003 Map(vectorType -> dense, length -> 4, values -> List(94290.0, 94290.0, 0.0, 0.0)) 97942.57629518774 94290 Map(vectorType -> dense, length -> 4, values -> List(96744.0, 97244.0, 0.0, 0.0)) 99990.3549342174 97244 Map(vectorType -> dense, length -> 4, values -> List(98381.0, 98881.0, 0.0, 0.0)) 99990.3549342174 98881 Map(vectorType -> dense, length -> 4, values -> List(105845.0, 108345.0, 0.0, 0.0)) 102156.40497854326 108345 Map(vectorType -> dense, length -> 4, values -> List(75619.0, 86054.0, 0.0, 0.0)) 71905.61550124122 86054 Map(vectorType -> dense, length -> 4, values -> List(105938.0, 108042.0, 0.0, 0.0)) 102156.40497854326 108042 Map(vectorType -> dense, length -> 4, values -> List(107437.0, 107437.0, 0.0, 0.0)) 102156.40497854326 107437 Map(vectorType -> dense, length -> 4, values -> List(122192.0, 122692.0, 0.0, 0.0)) 123182.7653567704 122692 Map(vectorType -> dense, length -> 4, values 

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.70352
RMSE: 39531.400998


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     14572|          0|         0|     500|     15072|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     15283|        376|         0|       0|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 209112 Testing Rows: 88954


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4004|          0|         0|       0|      4004|     09/25/2018|       Alameda|[4004.0,4004.0,0....|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3410|          0|         0|       0|      3410|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      9438|          0|         0|       0|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3410.0,3410.0,0....| 3759.363725648066|      3410|
|[9438.0,9438.0,0....| 8713.887960484699|      9438|
|[20064.0,21064.0,...|19506.433914113604|     21064|
|[31487.0,31487.0,...|30844.015892887506|     31487|
|[38893.0,54549.0,...|56328.580476103474|     54549|
|[50218.0,50440.0,...| 51156.30568874321|     50440|
|[63588.0,63588.0,...| 65941.46413005468|     63588|
|[75950.0,76450.0,...| 73285.16019050876|     76450|
|[76125.0,76125.0,...| 73285.16019050876|     76125|
|[97522.0,99522.0,...|103375.76322231651|     99522|
|[111230.0,111730....|117613.04058475712|    111730|
|[80971.0,81471.0,...| 82188.37631909897|     81471|
|[53364.0,53864.0,...|  52144.3241810765|     53864|
|[61874.0,62374.0,...| 60584.84745492411|     62374|
|[71256.0,71773.0,...|  72021.4481875641|     71773|
|[12716.0,12716.0,...|12205.117358498992|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3410.0,3410.0,0....| 3759.363725648066|      3410|
|[9438.0,9438.0,0....| 8713.887960484699|      9438|
|[20064.0,21064.0,...|19506.433914113604|     21064|
|[31487.0,31487.0,...|30844.015892887506|     31487|
|[38893.0,54549.0,...|56328.580476103474|     54549|
|[50218.0,50440.0,...| 51156.30568874321|     50440|
|[63588.0,63588.0,...| 65941.46413005468|     63588|
|[75950.0,76450.0,...| 73285.16019050876|     76450|
|[76125.0,76125.0,...| 73285.16019050876|     76125|
|[97522.0,99522.0,...|103375.76322231651|     99522|
|[111230.0,111730....|117613.04058475712|    111730|
|[80971.0,81471.0,...| 82188.37631909897|     81471|
|[53364.0,53864.0,...|  52144.3241810765|     53864|
|[61874.0,62374.0,...| 60584.84745492411|     62374|
|[71256.0,71773.0,...|  72021.4481875641|     71773|
|[12716.0,12716.0,...|12205.117358498992|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.841086
RMSE: 28691.169656


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3410.0,3410.0,0....| 3759.363725648066|      3410|
|[9438.0,9438.0,0....| 8713.887960484699|      9438|
|[20064.0,21064.0,...|19506.433914113604|     21064|
|[31487.0,31487.0,...|30844.015892887506|     31487|
|[38893.0,54549.0,...|56328.580476103474|     54549|
|[50218.0,50440.0,...| 51156.30568874321|     50440|
|[63588.0,63588.0,...| 65941.46413005468|     63588|
|[75950.0,76450.0,...| 73285.16019050876|     76450|
|[76125.0,76125.0,...| 73285.16019050876|     76125|
|[97522.0,99522.0,...|103375.76322231651|     99522|
|[111230.0,111730....|117613.04058475712|    111730|
|[80971.0,81471.0,...| 82188.37631909897|     81471|
|[53364.0,53864.0,...|  52144.3241810765|     53864|
|[61874.0,62374.0,...| 60584.84745492411|     62374|
|[71256.0,71773.0,...|  72021.4481875641|     71773|
|[12716.0,12716.0,...|12205.117358498992|     

In [0]:
# Code Break for 2018

#UC 2018

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2018_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2018_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Tut-Gship 0 0 null 13794 456 0 0 14250 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 39328 3931 0 2080 45339 3273 0 0 18273 21546 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 29257 0 0 0 29257 2341 0 0 6982 9323 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3208 0 0 0 3208 0 0 0 403 403 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 32868 542 0 2471 35881 2629 0 0 9171 11800 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51335 0 0 0 51335 3148 0 0 9818 12966 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 6174 0 0 652 6826 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 3 0 0 null 14760 0 0 0 14760 0 0 0 773 773 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 52810 310 0 500 53620 4225 0 0 25489 29714 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Lect-Ay|Teacher-Unex|Lect In Summer Session|Lect-Ay-1/10 0 0 null 49035 0 0 29033 78068 3923 0 217 6429 10569 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Admissions Recrmt Spec 3 0 0 null 69647 0 0 0 69647 5572 0 0 13223 18795 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Acad Achievement Cnslr 2 0 0 null 58822 0 0 0 58822 4706 0 0 6335 11041 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benef

In [0]:
# Create a view or table

temp_table_name = "2018_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     13794|        456|         0|       0|     14250|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     39328|       3931|         0|    2080|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 214093 Testing Rows: 91914


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3208|          0|         0|       0|      3208|     09/24/2019|       Alameda|[3208.0,3208.0,0....|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_13829860da30, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 93906.5)
     If (feature 1 <= 34899.5)
      Predict: 9351.719867279406
     Else (feature 1 > 34899.5)
      If (feature 1 <= 70679.5)
       Predict: 52489.983867221315
      Else (feature 1 > 70679.5)
       If (feature 1 <= 157049.0)
        If (feature 1 <= 88810.0)
         Predict: 79028.53851884964
        Else (feature 1 > 88810.0)
         Predict: 99851.07183056872
       Else (feature 1 > 157049.0)
        If (feature 1 <= 202515.0)
         Predict: 180210.52777777778
        Else (feature 1 > 202515.0)
         Predict: 303816.96992481203
    Else (feature 0 > 93906.5)
     Predict: 175805.76333027243
  Tree 1 (weight 1.0):
    If (feature 1 <= 115053.0)
     If (feature 0 <= 37639.5)
      If (feature 0 <= 14162.5)
       Predict: 4728.984499002181
      Else (feature 0 > 14162.5)
       If (feature 1 <= 29470.0)
        Predict: 21

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.533691 
 
 
 1 
 TotalWages 
 0.466309 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[14760.0,14760.0,...|  26820.3687865087|     14760|
|[32868.0,35881.0,...| 46585.07639277248|     35881|
|[39328.0,45339.0,...| 51764.79177505725|     45339|
|[52810.0,53620.0,...| 54438.73222151445|     53620|
|[43531.0,46373.0,...| 51764.79177505725|     46373|
|[67843.0,69569.0,...|  63598.8313361302|     69569|
|[68977.0,68977.0,...|  63598.8313361302|     68977|
|[73193.0,77291.0,...| 70674.84353386456|     77291|
|[73288.0,76938.0,...| 70674.84353386456|     76938|
|[92085.0,92085.0,...| 78996.10698509566|     92085|
|[87867.0,88867.0,...| 78996.10698509566|     88867|
|[123549.0,123549....| 126264.2169914633|    123549|
|[91044.0,93494.0,...| 78996.10698509566|     93494|
|[19724.0,19762.0,...|29458.608022672568|     19762|
|[25060.0,27098.0,...|32586.789912763583|     27098|
|[68088.0,68588.0,...|  63598.8313361302|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(14760.0, 14760.0, 0.0, 0.0)) 26820.3687865087 14760 Map(vectorType -> dense, length -> 4, values -> List(32868.0, 35881.0, 0.0, 0.0)) 46585.07639277248 35881 Map(vectorType -> dense, length -> 4, values -> List(39328.0, 45339.0, 0.0, 0.0)) 51764.79177505725 45339 Map(vectorType -> dense, length -> 4, values -> List(52810.0, 53620.0, 0.0, 0.0)) 54438.73222151445 53620 Map(vectorType -> dense, length -> 4, values -> List(43531.0, 46373.0, 0.0, 0.0)) 51764.79177505725 46373 Map(vectorType -> dense, length -> 4, values -> List(67843.0, 69569.0, 0.0, 0.0)) 63598.8313361302 69569 Map(vectorType -> dense, length -> 4, values -> List(68977.0, 68977.0, 0.0, 0.0)) 63598.8313361302 68977 Map(vectorType -> dense, length -> 4, values -> List(73193.0, 77291.0, 0.0, 0.0)) 70674.84353386456 77291 Map(vectorType -> dense, length -> 4, values -> List(73288.0, 76938.0, 0.0, 0.0)) 70674.84353386456 76938 Map(vectorType -> dense, length -> 4, values -> List(92085.0, 92085.0, 0.0, 0.0)) 78996.10698509566 92085 Map(vectorType -> dense, length -> 4, values -> List(87867.0, 88867.0, 0.0, 0.0)) 78996.10698509566 88867 Map(vectorType -> dense, length -> 4, values -> List(123549.0, 123549.0, 0.0, 0.0)) 126264.2169914633 123549 Map(vectorType -> dense, length -> 4, values -> List(91044.0, 93494.0, 0.0, 0.0)) 78996.10698509566 93494 Map(vectorType -> dense, length -> 4, values -> List(19724.0, 19762.0, 0.0, 0.0)) 29458.608022672568 19762 Map(vectorType -> dense, length -> 4, values -> List(25060.0, 27098.0, 0.0, 0.0)) 32586.789912763583 27098 Map(vectorType -> dense, length -> 4, values -> List(68088.0, 68588.0, 0.0, 0.0)) 63598.8313361302 68588 Map(vectorType -> dense, length -> 4, values -> List(69455.0, 69455.0, 0.0, 0.0)) 63598.8313361302 69455 Map(vectorType -> dense, length -> 4, values -> List(77901.0, 80401.0, 0.0, 0.0)) 71857.12823130313 80401 Map(vectorType -> dense, length -> 4, values -> List(1197.0, 1197.0, 0.0, 0.0)) 18054.34424744147 1197 Map(vectorType -> dense, length -> 4, values -> List(68533.0, 69033.0, 0.0, 0.0)) 63598.8313361302 69033 Map(vectorType -> dense, length -> 4, values -> List(68823.0, 68823.0, 0.0, 0.0)) 63598.8313361302 68823 Map(vectorType -> dense, length -> 4, values -> List(68850.0, 68850.0, 0.0, 0.0)) 63598.8313361302 68850 Map(vectorType -> dense, length -> 4, values -> List(70686.0, 70686.0, 0.0, 0.0)) 68044.7066921918 70686 Map(vectorType -> dense, length -> 4, values -> List(74925.0, 74925.0, 0.0, 0.0)) 70674.84353386456 74925 Map(vectorType -> dense, length -> 4, values -> List(76002.0, 76502.0, 0.0, 0.0)) 70674.84353386456 76502 Map(vectorType -> dense, length -> 4, values -> List(76589.0, 77089.0, 0.0, 0.0)) 70674.84353386456 77089 Map(vectorType -> dense, length -> 4, values -> List(79533.0, 80033.0, 0.0, 0.0)) 71857.12823130313 80033 Map(vectorType -> dense, length -> 4, values -> List(80680.0, 80680.0, 0.0, 0.0)) 71857.12823130313 80680 Map(vectorType -> dense, length -> 4, values -> List(82336.0, 82336.0, 0.0, 0.0)) 71857.12823130313 82336 Map(vectorType -> dense, length -> 4, values -> List(83958.0, 83958.0, 0.0, 0.0)) 75451.53776871294 83958 Map(vectorType -> dense, length -> 4, values -> List(88209.0, 88209.0, 0.0, 0.0)) 75451.53776871294 88209 Map(vectorType -> dense, length -> 4, values -> List(12927.0, 13784.0, 0.0, 0.0)) 23640.930171143027 13784 Map(vectorType -> dense, length -> 4, values -> List(91763.0, 96631.0, 0.0, 0.0)) 78996.10698509566 96631 Map(vectorType -> dense, length -> 4, values -> List(95738.0, 95738.0, 0.0, 0.0)) 100747.55097480614 95738 Map(vectorType -> dense, length -> 4, values -> List(99581.0, 101581.0, 0.0, 0.0)) 103461.68679757716 101581 Map(vectorType -> dense, length -> 4, values -> List(12558.0, 12558.0, 0.0, 0.0)) 23640.930171143027 12558 Map(vectorType -> dense, length -> 4, values -> List(104355.0, 104855.0, 0.0, 0.0)) 103461.68679757716 104855 Map(vectorType -> dense, length -> 4, values ->

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.705716
RMSE: 40303.009622


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     13794|        456|         0|       0|     14250|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     39328|       3931|         0|    2080|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 214809 Testing Rows: 91198


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      6174|          0|         0|     652|      6826|     09/24/2019|       Alameda|[6174.0,6826.0,0....|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3208|          0|         0|       0|      3208|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      6174|          0|         0|     652|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.874567
RMSE: 25486.684664


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
### Code Break for 2019

#UC 2019

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2019_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 3|Teachg Asst-1/10-Gship 0 0 null 28780 17 0 0 28797 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 30656 198 0 549 31403 1642 0 0 1641 3283 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 19543 0 0 0 19543 841 0 0 8169 9010 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 46179 0 0 3205 49384 2578 0 0 20633 23211 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5154 0 0 0 5154 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 56923 0 0 2000 58923 3034 0 0 9199 12233 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 24552 0 0 626 25178 0 0 0 875 875 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 21842 0 0 0 21842 999 0 0 2805 3804 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 15618 0 0 0 15618 0 0 0 1860 1860 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Acad Achievement Cnslr 3 0 0 null 56162 0 0 5015 61177 4894 0 0 23636 28530 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 39770 22 0 500 40292 2046 0 0 7270 9316 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6568 0 0 0 6568 0 0 0 1175 1175 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of Cal

In [0]:
# Create a view or table

temp_table_name = "2019_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     28780|         17|         0|       0|     28797|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     30656|        198|         0|     549|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 218402 Testing Rows: 93716


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      5154|          0|         0|       0|      5154|     10/13/2020|       Alameda|[5154.0,5154.0,0....|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_b534f9272593, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 98089.5)
     If (feature 1 <= 36189.0)
      Predict: 10094.554368642057
     Else (feature 1 > 36189.0)
      If (feature 1 <= 72867.5)
       Predict: 54177.03419995421
      Else (feature 1 > 72867.5)
       If (feature 1 <= 141846.0)
        If (feature 0 <= 85824.5)
         Predict: 83451.15358668765
        Else (feature 0 > 85824.5)
         Predict: 97394.55391120508
       Else (feature 1 > 141846.0)
        If (feature 0 <= 53528.5)
         Predict: 272079.8333333333
        Else (feature 0 > 53528.5)
         Predict: 192983.2275862069
    Else (feature 0 > 98089.5)
     Predict: 185811.05585580322
  Tree 1 (weight 1.0):
    If (feature 1 <= 121506.0)
     If (feature 0 <= 39013.5)
      If (feature 0 <= 15349.0)
       Predict: 5160.593455039367
      Else (feature 0 > 15349.0)
       If (feature 1 <= 31066.5)
        Predict: 23506.

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.530359 
 
 
 1 
 TotalWages 
 0.469641 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[24552.0,25178.0,...|31258.330117311627|     25178|
|[30656.0,31403.0,...| 36850.95936831949|     31403|
|[38632.0,38632.0,...| 46885.71085722052|     38632|
|[56923.0,58923.0,...|  57154.0833324739|     58923|
|[40304.0,45988.0,...| 54357.61281570264|     45988|
|[61525.0,63525.0,...| 59951.05411047019|     63525|
|[66002.0,68002.0,...| 62915.74816638008|     68002|
|[67880.0,67880.0,...| 62915.74816638008|     67880|
|[68889.0,68889.0,...| 63848.92798469977|     68889|
|[68977.0,68977.0,...| 63848.92798469977|     68977|
|[82537.0,84537.0,...| 75757.01525228587|     84537|
|[83103.0,85103.0,...| 75757.01525228587|     85103|
|[85296.0,86296.0,...| 75757.01525228587|     86296|
|[94090.0,94090.0,...| 81282.13932058259|     94090|
|[100192.0,107231....|107438.07883856868|    107231|
|[91567.0,91567.0,...| 81282.13932058259|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(24552.0, 25178.0, 0.0, 0.0)) 31258.330117311627 25178 Map(vectorType -> dense, length -> 4, values -> List(30656.0, 31403.0, 0.0, 0.0)) 36850.95936831949 31403 Map(vectorType -> dense, length -> 4, values -> List(38632.0, 38632.0, 0.0, 0.0)) 46885.71085722052 38632 Map(vectorType -> dense, length -> 4, values -> List(56923.0, 58923.0, 0.0, 0.0)) 57154.0833324739 58923 Map(vectorType -> dense, length -> 4, values -> List(40304.0, 45988.0, 0.0, 0.0)) 54357.61281570264 45988 Map(vectorType -> dense, length -> 4, values -> List(61525.0, 63525.0, 0.0, 0.0)) 59951.05411047019 63525 Map(vectorType -> dense, length -> 4, values -> List(66002.0, 68002.0, 0.0, 0.0)) 62915.74816638008 68002 Map(vectorType -> dense, length -> 4, values -> List(67880.0, 67880.0, 0.0, 0.0)) 62915.74816638008 67880 Map(vectorType -> dense, length -> 4, values -> List(68889.0, 68889.0, 0.0, 0.0)) 63848.92798469977 68889 Map(vectorType -> dense, length -> 4, values -> List(68977.0, 68977.0, 0.0, 0.0)) 63848.92798469977 68977 Map(vectorType -> dense, length -> 4, values -> List(82537.0, 84537.0, 0.0, 0.0)) 75757.01525228587 84537 Map(vectorType -> dense, length -> 4, values -> List(83103.0, 85103.0, 0.0, 0.0)) 75757.01525228587 85103 Map(vectorType -> dense, length -> 4, values -> List(85296.0, 86296.0, 0.0, 0.0)) 75757.01525228587 86296 Map(vectorType -> dense, length -> 4, values -> List(94090.0, 94090.0, 0.0, 0.0)) 81282.13932058259 94090 Map(vectorType -> dense, length -> 4, values -> List(100192.0, 107231.0, 0.0, 0.0)) 107438.07883856868 107231 Map(vectorType -> dense, length -> 4, values -> List(91567.0, 91567.0, 0.0, 0.0)) 81282.13932058259 91567 Map(vectorType -> dense, length -> 4, values -> List(95013.0, 96013.0, 0.0, 0.0)) 81282.13932058259 96013 Map(vectorType -> dense, length -> 4, values -> List(106724.0, 106724.0, 0.0, 0.0)) 107438.07883856868 106724 Map(vectorType -> dense, length -> 4, values -> List(111832.0, 112832.0, 0.0, 0.0)) 108294.75846818757 112832 Map(vectorType -> dense, length -> 4, values -> List(118257.0, 119257.0, 0.0, 0.0)) 108294.75846818757 119257 Map(vectorType -> dense, length -> 4, values -> List(94328.0, 95328.0, 0.0, 0.0)) 81282.13932058259 95328 Map(vectorType -> dense, length -> 4, values -> List(57451.0, 57951.0, 0.0, 0.0)) 57154.0833324739 57951 Map(vectorType -> dense, length -> 4, values -> List(64846.0, 67346.0, 0.0, 0.0)) 62915.74816638008 67346 Map(vectorType -> dense, length -> 4, values -> List(69795.0, 70795.0, 0.0, 0.0)) 63848.92798469977 70795 Map(vectorType -> dense, length -> 4, values -> List(72378.0, 72878.0, 0.0, 0.0)) 68647.11082352244 72878 Map(vectorType -> dense, length -> 4, values -> List(72708.0, 73208.0, 0.0, 0.0)) 68647.11082352244 73208 Map(vectorType -> dense, length -> 4, values -> List(75470.0, 75470.0, 0.0, 0.0)) 68647.11082352244 75470 Map(vectorType -> dense, length -> 4, values -> List(75940.0, 75940.0, 0.0, 0.0)) 74989.18556620902 75940 Map(vectorType -> dense, length -> 4, values -> List(77177.0, 77177.0, 0.0, 0.0)) 74989.18556620902 77177 Map(vectorType -> dense, length -> 4, values -> List(79297.0, 83181.0, 0.0, 0.0)) 75757.01525228587 83181 Map(vectorType -> dense, length -> 4, values -> List(82098.0, 82598.0, 0.0, 0.0)) 75757.01525228587 82598 Map(vectorType -> dense, length -> 4, values -> List(85886.0, 88570.0, 0.0, 0.0)) 78385.6746276605 88570 Map(vectorType -> dense, length -> 4, values -> List(86633.0, 86633.0, 0.0, 0.0)) 78385.6746276605 86633 Map(vectorType -> dense, length -> 4, values -> List(94875.0, 94875.0, 0.0, 0.0)) 81282.13932058259 94875 Map(vectorType -> dense, length -> 4, values -> List(100874.0, 105041.0, 0.0, 0.0)) 107438.07883856868 105041 Map(vectorType -> dense, length -> 4, values -> List(14610.0, 14610.0, 0.0, 0.0)) 24580.859429970493 14610 Map(vectorType -> dense, length -> 4, values -> List(131662.0, 141662.0, 0.0, 0.0)) 128726.48379477602 141662 Map(vectorType -> dense, len

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.745072
RMSE: 37811.234799


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     28780|         17|         0|       0|     28797|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     30656|        198|         0|     549|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 218151 Testing Rows: 93967


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      5154|          0|         0|       0|      5154|     10/13/2020|       Alameda|[5154.0,5154.0,0....|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      6568|          0|         0|       0|      6568|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     19543|          0|         0|       0|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.841562
RMSE: 31006.525910


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
### Code break for 2020

#UC 2020

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2020_UniversityOfCalifornia.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 500 59819 2733 0 0 20704 23437 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 0 59319 2733 0 0 9008 11741 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 57338 0 0 2140 59478 2641 0 0 7787 10428 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 230 0 500 60049 2733 0 0 7749 10482 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 500 59819 2733 0 0 7329 10062 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1609 0 0 0 1609 74 0 0 3843 3917 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 31605 0 0 0 31605 1456 0 0 7749 9205 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47539 341 0 500 48380 2191 0 0 8166 10357 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 53807 0 0 0 53807 1521 0 0 5845 7366 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 68977 0 0 0 68977 5600 0 0 7310 12910 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 66000 0 0 0 66000 3017 0 0 11197 14214 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 69000 0 0 0 69000 5602 0 0 20813 26415 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley

In [0]:
# Create a view or table

temp_table_name = "2020_UniversityOfCalifornia_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|     500|     59819|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|       0|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 205187 Testing Rows: 87837


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1609|          0|         0|       0|      1609|     09/28/2021|       Alameda|[1609.0,1609.0,0....|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_990e2eec0bbf, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 105671.0)
     If (feature 1 <= 41022.0)
      Predict: 11747.876844009703
     Else (feature 1 > 41022.0)
      If (feature 1 <= 75306.0)
       Predict: 57710.45734586795
      Else (feature 1 > 75306.0)
       If (feature 1 <= 149065.5)
        If (feature 0 <= 94546.5)
         Predict: 87983.6094144018
        Else (feature 0 > 94546.5)
         Predict: 106418.84902172239
       Else (feature 1 > 149065.5)
        If (feature 0 <= 4.5)
         Predict: 686135.875
        Else (feature 0 > 4.5)
         Predict: 204671.91620111733
    Else (feature 0 > 105671.0)
     Predict: 193606.7584917044
  Tree 1 (weight 1.0):
    If (feature 1 <= 114539.5)
     If (feature 0 <= 37603.0)
      If (feature 0 <= 13208.5)
       Predict: 4730.966486517815
      Else (feature 0 > 13208.5)
       If (feature 1 <= 25351.5)
        Predict: 19393.008334530823


In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.527156 
 
 
 1 
 TotalWages 
 0.472844 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[31605.0,31605.0,...| 38718.46244142247|     31605|
|[5333.0,5333.0,0....| 22037.38581282198|      5333|
|[14424.0,14424.0,...| 29335.75584447417|     14424|
|[39754.0,40254.0,...| 48101.25604245749|     40254|
|[60362.0,60362.0,...|63224.802445871734|     60362|
|[65000.0,65000.0,...|63224.802445871734|     65000|
|[65000.0,65500.0,...|63224.802445871734|     65500|
|[68977.0,68977.0,...|63224.802445871734|     68977|
|[69000.0,69000.0,...|63224.802445871734|     69000|
|[83988.0,83988.0,...| 76900.38344268584|     83988|
|[84564.0,84564.0,...| 76900.38344268584|     84564|
|[99360.0,99360.0,...|  87497.1110268934|     99360|
|[95556.0,95556.0,...|  87497.1110268934|     95556|
|[107997.0,107997....| 112347.7007042487|    107997|
|[48771.0,48771.0,...|58243.817260296724|     48771|
|[65166.0,65666.0,...|63224.802445871734|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(31605.0, 31605.0, 0.0, 0.0)) 38718.46244142247 31605 Map(vectorType -> dense, length -> 4, values -> List(5333.0, 5333.0, 0.0, 0.0)) 22037.38581282198 5333 Map(vectorType -> dense, length -> 4, values -> List(14424.0, 14424.0, 0.0, 0.0)) 29335.75584447417 14424 Map(vectorType -> dense, length -> 4, values -> List(39754.0, 40254.0, 0.0, 0.0)) 48101.25604245749 40254 Map(vectorType -> dense, length -> 4, values -> List(60362.0, 60362.0, 0.0, 0.0)) 63224.802445871734 60362 Map(vectorType -> dense, length -> 4, values -> List(65000.0, 65000.0, 0.0, 0.0)) 63224.802445871734 65000 Map(vectorType -> dense, length -> 4, values -> List(65000.0, 65500.0, 0.0, 0.0)) 63224.802445871734 65500 Map(vectorType -> dense, length -> 4, values -> List(68977.0, 68977.0, 0.0, 0.0)) 63224.802445871734 68977 Map(vectorType -> dense, length -> 4, values -> List(69000.0, 69000.0, 0.0, 0.0)) 63224.802445871734 69000 Map(vectorType -> dense, length -> 4, values -> List(83988.0, 83988.0, 0.0, 0.0)) 76900.38344268584 83988 Map(vectorType -> dense, length -> 4, values -> List(84564.0, 84564.0, 0.0, 0.0)) 76900.38344268584 84564 Map(vectorType -> dense, length -> 4, values -> List(99360.0, 99360.0, 0.0, 0.0)) 87497.1110268934 99360 Map(vectorType -> dense, length -> 4, values -> List(95556.0, 95556.0, 0.0, 0.0)) 87497.1110268934 95556 Map(vectorType -> dense, length -> 4, values -> List(107997.0, 107997.0, 0.0, 0.0)) 112347.7007042487 107997 Map(vectorType -> dense, length -> 4, values -> List(48771.0, 48771.0, 0.0, 0.0)) 58243.817260296724 48771 Map(vectorType -> dense, length -> 4, values -> List(65166.0, 65666.0, 0.0, 0.0)) 63224.802445871734 65666 Map(vectorType -> dense, length -> 4, values -> List(66997.0, 66997.0, 0.0, 0.0)) 63224.802445871734 66997 Map(vectorType -> dense, length -> 4, values -> List(69846.0, 70346.0, 0.0, 0.0)) 64041.632550556635 70346 Map(vectorType -> dense, length -> 4, values -> List(78190.0, 78690.0, 0.0, 0.0)) 74674.56947504147 78690 Map(vectorType -> dense, length -> 4, values -> List(79327.0, 81327.0, 0.0, 0.0)) 74674.56947504147 81327 Map(vectorType -> dense, length -> 4, values -> List(79415.0, 79415.0, 0.0, 0.0)) 74674.56947504147 79415 Map(vectorType -> dense, length -> 4, values -> List(80295.0, 80990.0, 0.0, 0.0)) 74674.56947504147 80990 Map(vectorType -> dense, length -> 4, values -> List(5397.0, 5397.0, 0.0, 0.0)) 22037.38581282198 5397 Map(vectorType -> dense, length -> 4, values -> List(14000.0, 14000.0, 0.0, 0.0)) 29335.75584447417 14000 Map(vectorType -> dense, length -> 4, values -> List(55293.0, 58104.0, 0.0, 0.0)) 59192.65511235197 58104 Map(vectorType -> dense, length -> 4, values -> List(55958.0, 71173.0, 0.0, 0.0)) 60883.64076101415 71173 Map(vectorType -> dense, length -> 4, values -> List(78516.0, 79016.0, 0.0, 0.0)) 74674.56947504147 79016 Map(vectorType -> dense, length -> 4, values -> List(78516.0, 79016.0, 0.0, 0.0)) 74674.56947504147 79016 Map(vectorType -> dense, length -> 4, values -> List(82704.0, 89407.0, 0.0, 0.0)) 76900.38344268584 89407 Map(vectorType -> dense, length -> 4, values -> List(88246.0, 91658.0, 0.0, 0.0)) 83481.00047198062 91658 Map(vectorType -> dense, length -> 4, values -> List(89277.0, 89777.0, 0.0, 0.0)) 82135.17638096213 89777 Map(vectorType -> dense, length -> 4, values -> List(100542.0, 108542.0, 0.0, 0.0)) 87497.1110268934 108542 Map(vectorType -> dense, length -> 4, values -> List(103308.0, 109141.0, 0.0, 0.0)) 87497.1110268934 109141 Map(vectorType -> dense, length -> 4, values -> List(32579.0, 32579.0, 0.0, 0.0)) 39326.781696356935 32579 Map(vectorType -> dense, length -> 4, values -> List(59384.0, 66261.0, 0.0, 0.0)) 61606.57923916627 66261 Map(vectorType -> dense, length -> 4, values -> List(108650.0, 110650.0, 0.0, 0.0)) 112347.7007042487 110650 Map(vectorType -> dense, length -> 4, values -> List(111372.0, 111372.0, 0.0, 0.0)) 112347.7007042487 111372 Map(vectorType -> dense, length -> 

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.700948
RMSE: 44771.744477


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|     500|     59819|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|       0|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 205140 Testing Rows: 87884


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     31605|          0|         0|       0|     31605|     09/28/2021|       Alameda|[31605.0,31605.0,...|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)
#%pyspark
model = cv.fit(train)
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1609|          0|         0|       0|      1609|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     53807|          0|         0|       0|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1609.0,1609.0,0....|1451.3189081635212|      1609|
|[53807.0,53807.0,...| 53763.71102006211|     53807|
|[57338.0,59478.0,...|61401.318364748084|     59478|
|[59319.0,59819.0,...|61401.318364748084|     59819|
|[5333.0,5333.0,0....| 4439.055080100617|      5333|
|[39754.0,40254.0,...|38890.430714395756|     40254|
|[61632.0,90400.0,...| 85962.13210334958|     90400|
|[65000.0,65500.0,...| 66144.91013867171|     65500|
|[66000.0,66000.0,...| 66144.91013867171|     66000|
|[68977.0,68977.0,...| 66144.91013867171|     68977|
|[69000.0,69000.0,...| 66144.91013867171|     69000|
|[72000.0,72000.0,...| 72255.75723957931|     72000|
|[83988.0,83988.0,...|  85904.9577999301|     83988|
|[90933.0,90933.0,...| 95628.87594153082|     90933|
|[90944.0,91444.0,...| 95628.87594153082|     91444|
|[99672.0,99672.0,...| 98105.31925848628|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.85207
RMSE: 30924.561561


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1609.0,1609.0,0....|1451.3189081635212|      1609|
|[53807.0,53807.0,...| 53763.71102006211|     53807|
|[57338.0,59478.0,...|61401.318364748084|     59478|
|[59319.0,59819.0,...|61401.318364748084|     59819|
|[5333.0,5333.0,0....| 4439.055080100617|      5333|
|[39754.0,40254.0,...|38890.430714395756|     40254|
|[61632.0,90400.0,...| 85962.13210334958|     90400|
|[65000.0,65500.0,...| 66144.91013867171|     65500|
|[66000.0,66000.0,...| 66144.91013867171|     66000|
|[68977.0,68977.0,...| 66144.91013867171|     68977|
|[69000.0,69000.0,...| 66144.91013867171|     69000|
|[72000.0,72000.0,...| 72255.75723957931|     72000|
|[83988.0,83988.0,...|  85904.9577999301|     83988|
|[90933.0,90933.0,...| 95628.87594153082|     90933|
|[90944.0,91444.0,...| 95628.87594153082|     91444|
|[99672.0,99672.0,...| 98105.31925848628|     